In [17]:
from collections import OrderedDict
import pandas as pd
import numpy as np

import torch
import torch.nn as nn
from torch.utils.data import Dataset, DataLoader
from torch.nn import functional as F
from torchsummary import summary

from plotly import express as px
from plotly import graph_objects as go
from plotly import subplots as sp

from sklearn.model_selection import train_test_split


In [18]:
data = pd.read_csv("train.csv", index_col="id").rename(
    columns={
        "FAVC": "Frequent consumption of high caloric food",
        "FCVC": "Frequency of consumption of vegetables",
        "NCP": "Number of main meals",
        "CAEC": "Consumption of food between meals",
        "CH2O": "Consumption of water daily",
        "SCC": "Calories consumption monitoring",
        "FAF": "Physical activity frequency",
        "TUE": "Time using technology devices",
        "CALC": "Consumption of alcohol",
        "MTRANS": "Transportation used",
    }
)

data = pd.concat(
    [
        data[data["NObeyesdad"] == value].sample(2400)
        for value in data["NObeyesdad"].unique().tolist()
    ]
)


In [19]:
px.histogram(
    data,
    x="NObeyesdad",
)


In [20]:
data = data.assign(
    **{
        "Age": data.Age.round(),
        "Height": (data.Height * 100).round(),
        "Weight": data.Weight.round(),
        "Frequency of consumption of vegetables": data[
            "Frequency of consumption of vegetables"
        ]
        .round()
        .astype("int"),
        "Number of main meals": data["Number of main meals"].round().astype("int"),
        "Consumption of water daily": 8
        * data["Consumption of water daily"].round().astype("int"),
        "Physical activity frequency": data["Physical activity frequency"]
        .round()
        .astype("int"),
        "Time using technology devices": data["Time using technology devices"]
        .round()
        .astype("int"),
        "BMI": lambda x: x["Weight"]
        / x["Height"]
        / np.where(
            x["Physical activity frequency"] == 0,
            1,
            x["Physical activity frequency"],
        ),
    }
)


In [21]:
data.describe()


Age        Height        Weight   
count  16800.000000  16800.000000  16800.000000  \
mean      23.714345    169.968810     84.811369   
std        5.867995      8.802222     25.585075   
min       14.000000    145.000000     39.000000   
25%       20.000000    163.000000     65.000000   
50%       22.000000    170.000000     82.000000   
75%       26.000000    176.000000    106.000000   
max       61.000000    198.000000    165.000000   

       Frequency of consumption of vegetables  Number of main meals   
count                            16800.000000          16800.000000  \
mean                                 2.413869              2.746845   
std                                  0.563983              0.752492   
min                                  1.000000              1.000000   
25%                                  2.000000              3.000000   
50%                                  2.000000              3.000000   
75%                                  3.000000              3.000000   
max                                  3.000000              4.000000   

       Consumption of water daily  Physical activity frequency   
count                16800.000000                 16800.000000  \
mean                    16.261905                     1.017798   
std                      5.343243                     0.867825   
min                      8.000000                     0.000000   
25%                     16.000000                     0.000000   
50%                     16.000000                     1.000000   
75%                     16.000000                     2.000000   
max                     24.000000                     3.000000   

       Time using technology devices           BMI  
count                   16800.000000  16800.000000  
mean                        0.634405      0.427683  
std                         0.666948      0.177992  
min                         0.000000      0.075581  
25%                         0.000000      0.283422  
50%                         1.000000      0.430795  
75%                         1.000000      0.586592  
max                         2.000000      0.953757

In [22]:
data.info()


<class 'pandas.core.frame.DataFrame'>
Index: 16800 entries, 19053 to 3094
Data columns (total 18 columns):
 #   Column                                     Non-Null Count  Dtype  
---  ------                                     --------------  -----  
 0   Gender                                     16800 non-null  object 
 1   Age                                        16800 non-null  float64
 2   Height                                     16800 non-null  float64
 3   Weight                                     16800 non-null  float64
 4   family_history_with_overweight             16800 non-null  object 
 5   Frequent consumption of high caloric food  16800 non-null  object 
 6   Frequency of consumption of vegetables     16800 non-null  int32  
 7   Number of main meals                       16800 non-null  int32  
 8   Consumption of food between meals          16800 non-null  object 
 9   SMOKE                                      16800 non-null  object 
 10  Consumption of water dai

In [23]:
data.head()


Gender   Age  Height  Weight family_history_with_overweight   
id                                                                   
19053  Female  21.0   172.0    79.0                            yes  \
20585    Male  23.0   170.0    84.0                            yes   
10221  Female  23.0   150.0    63.0                            yes   
11296    Male  34.0   176.0    80.0                            yes   
17824    Male  32.0   182.0    91.0                            yes   

      Frequent consumption of high caloric food   
id                                                
19053                                       yes  \
20585                                       yes   
10221                                        no   
11296                                       yes   
17824                                       yes   

       Frequency of consumption of vegetables  Number of main meals   
id                                                                    
19053                                       2                     2  \
20585                                       2                     2   
10221                                       2                     1   
11296                                       2                     3   
17824                                       2                     3   

      Consumption of food between meals SMOKE  Consumption of water daily   
id                                                                          
19053                         Sometimes    no                          16  \
20585                         Sometimes    no                          16   
10221                         Sometimes    no                          16   
11296                         Sometimes    no                          16   
17824                         Sometimes    no                          16   

      Calories consumption monitoring  Physical activity frequency   
id                                                                   
19053                              no                            2  \
20585                              no                            1   
10221                              no                            0   
11296                              no                            1   
17824                              no                            1   

       Time using technology devices Consumption of alcohol   
id                                                            
19053                              1              Sometimes  \
20585                              0              Sometimes   
10221                              0                     no   
11296                              1                     no   
17824                              0              Sometimes   

         Transportation used           NObeyesdad       BMI  
id                                                           
19053  Public_Transportation  Overweight_Level_II  0.229651  
20585  Public_Transportation  Overweight_Level_II  0.494118  
10221  Public_Transportation  Overweight_Level_II  0.420000  
11296             Automobile  Overweight_Level_II  0.454545  
17824             Automobile  Overweight_Level_II  0.500000

In [24]:
# Made a key that I can use to identify the labels once I convert them to their respective index.
label_values = data.NObeyesdad.unique().tolist()


In [25]:
# Feature engineered data

updated_data = (
    pd.get_dummies(
        data.select_dtypes("object").drop(columns=["NObeyesdad"]), drop_first=True
    )
    .join(data.select_dtypes("number"))
    .join(data["NObeyesdad"].apply(label_values.index))
)


In [26]:
px.scatter_matrix(updated_data, color="NObeyesdad", height=5000, width=5000)
